# Data Wrangling with Python Datatable - Selecting Columns

This article highlights various ways to select columns in python datatable. The examples used here are based off the excellent [article](https://suzan.rbind.io/2018/01/dplyr-tutorial-1/) by [Susan Baert](https://twitter.com/SuzanBaert).

The data file can be accessed [here](https://github.com/samukweku/data-wrangling-blog/raw/master/_notebooks/Data_files/msleep.txt)

## **Selecting Columns**

### The Basics

In [10]:
from datatable import dt, f, ltype, stype
import re

file_path='Data_files/msleep.txt'
DT = dt.fread(file_path)
DT.head(5)

<Frame#7fb7f009ccc0 5x11>

You can select columns by name or position in the `j` section:

In [11]:
DT[:, 'genus'].head(5)

<Frame#7fb7e0d4aed0 5x1>

In [12]:
DT[:, 1].head()

<Frame#7fb7e0d459c0 10x1>

In [13]:
DT[:, -10].head()


<Frame#7fb7e102f5d0 10x1>

If you are selecting a single column, you can pass it into the brackets without specifying the `i` section:

In [14]:
DT['genus'].head(5)

<Frame#7fb7e102f0f0 5x1>

For the rest of this article, I will be focusing on column selection by name.

You can select columns by passing a list/tuple of the column names:

In [15]:
columns_to_select = ["name", "genus", "sleep_total", "awake"]
DT[:, columns_to_select].head(5)

<Frame#7fb7e102ff60 5x4>

You can pass a list/tuple of booleans:

In [16]:
columns_to_select = [True, True, False, False, False, True,False,True,True,False,False]
DT[:, columns_to_select].head(5)

<Frame#7fb7e0d4afc0 5x5>

You can select chunks of columns using python's [slice](https://docs.python.org/3/library/functions.html#slice) syntax or via the ``start:end`` shortcut:

In [17]:
DT[:, slice("name", "order")].head(5)

<Frame#7fb7e0d4a7b0 5x4>

In [18]:
DT[:, "name" : "order"].head(5)


<Frame#7fb7e102f9c0 5x4>

Multiple chunk selection is possible:

In [19]:
columns_to_select = [slice("name", "order"), slice("sleep_total", "sleep_cycle")]
DT[:, columns_to_select].head(5)

<Frame#7fb7e102f120 5x7>

For the shortcut notation, for multiple selections, it has to be prefixed with datatable's [f](https://datatable.readthedocs.io/en/latest/manual/f-expressions.html) symbol:

In [20]:
columns_to_select = [f["name" : "order", "sleep_total" : "sleep_cycle"]]
DT[:, columns_to_select].head(5)

<Frame#7fb7e0d4aa20 5x7>

To deselect/drop columns you can use the [remove](https://datatable.readthedocs.io/en/latest/manual/f-expressions.html#modifying-a-columnset) function:

In [21]:
columns_to_remove = [f["sleep_total" : "awake", "conservation"]]
DT[:, f[:].remove(columns_to_remove)].head(5)

<Frame#7fb7e0d45090 5x6>

You can deselect a whole chunk, and then re-add a column again; this combines the [remove](https://datatable.readthedocs.io/en/latest/manual/f-expressions.html#modifying-a-columnset) and [extend](https://datatable.readthedocs.io/en/latest/manual/f-expressions.html#modifying-a-columnset) functions:

In [22]:
DT[:, f[:].remove(f["name" : "awake"]).extend(f["conservation"])].head(5)

<Frame#7fb7e102fc60 5x3>

### Selecting Columns based on Partial Names

You can use python's string functions to filter for columns with partial matching:

In [23]:
columns_to_select = [name.startswith("sleep") for name in DT.names]
DT[:, columns_to_select].head(5)

<Frame#7fb7e102f7b0 5x3>

In [24]:
columns_to_select = ["eep" in name or name.endswith("wt") for name in DT.names]
DT[:, columns_to_select].head(5)

<Frame#7fb7e0ff3600 5x5>

### Selecting Columns based on Regex

Python's [re](https://docs.python.org/3/library/re.html) module can be used to select columns based on a regular expression:

In [25]:
# this returns a list of booleans
columns_to_select = [True if re.search(r"o.+er", name) else False for name in DT.names]
DT[:, columns_to_select].head(5)

<Frame#7fb7e0d45060 5x2>

### Selecting columns by their data type

You can pass a data type in the ``j`` section:

In [26]:
DT[:, str].head(5)

<Frame#7fb7e0d4aba0 5x5>

You can pass a list of data types:

In [27]:
DT[:, [int, float]].head(5)

<Frame#7fb7e0d4ab40 5x6>

You can also pass datatable's [stype](https://datatable.readthedocs.io/en/latest/api/stype.html#) or [ltype](https://datatable.readthedocs.io/en/latest/api/ltype.html#) data types:

In [28]:
DT[:, ltype.str].head(5)

<Frame#7fb7e0d4a990 5x5>

In [29]:
DT[:, stype.float64].head(5)

<Frame#7fb7e0d4aab0 5x6>

You can remove columns based on their data type:

In [30]:
columns_to_remove = [f[int, float]]
DT[:, f[:].remove(columns_to_remove)].head(5)

<Frame#7fb7e0ff3c30 5x5>

An alternative is to preselect the columns you intend to keep:

In [31]:
# creates a list of booleans
columns_to_select = [
    dtype not in (ltype.int, ltype.real)
    for _, dtype in zip(DT.names, DT.ltypes) 
]

DT[:, columns_to_select].head(5)

<Frame#7fb7e0d45120 5x5>

You could also iterate through the frame and check each column's type, before recombining with [cbind](https://datatable.readthedocs.io/en/latest/api/dt/cbind.html):

In [32]:
matching_frames = [frame for frame in DT if frame.ltypes[0] not in (ltype.real, ltype.int)]
dt.cbind(matching_frames).head(5)


<Frame#7fb7e102ff00 5x5>

Each column in a frame is treated as a frame, allowing for the list comprehension above.

You could also pass the `matching frames` to the `j` section of `DT`:

In [33]:
DT[:, matching_frames].head(5)

<Frame#7fb7e0d4ad20 5x5>

### Selecting columns by logical expressions

The ideas expressed in the previous section allows for more nifty column selection. 

Say we wish to select columns that are numeric, and have a mean greater than 10:

In [34]:
# returns a list of booleans
columns_to_select = [
    ltype in (ltype.real, ltype.int) and DT[name].mean()[0, 0] > 10
    for name, ltype in zip(DT.names, DT.ltypes)
]
DT[:, columns_to_select].head(5)

<Frame#7fb7e0d4a090 5x3>

The code above preselects the columns before passing it to datatable. Note the use of `[0,0]` to return a scalar value; this allows us to compare with the scalar value `10`.

Alternatively, in the list comprehension, instead of a list of booleans, you could return the column names:


In [35]:
columns_to_select = [
    name
    for name, ltype in zip(DT.names, DT.ltypes)
    if ltype in (ltype.real, ltype.int) and DT[name].mean()[0, 0] > 10
]
DT[:, columns_to_select].head(5)

<Frame#7fb7e0ff3480 5x3>


You could also iterate through the frame in a list comprehension and check each column, before recombining with [cbind](https://datatable.readthedocs.io/en/latest/api/dt/cbind.html):

In [36]:
matching_frames = [frame for frame in DT 
                    if frame.ltypes[0] in (ltype.int, ltype.real) 
                    and frame.mean()[0,0] > 10]
dt.cbind(matching_frames).head(5)

<Frame#7fb7e0d4ac60 5x3>

Instead of recombining with [cbind](https://datatable.readthedocs.io/en/latest/api/dt/cbind.html), you could pass the `matching_frames` to the ``j`` section:

In [37]:
DT[:, matching_frames].head(5)

<Frame#7fb7e0d4a450 5x3>

Let's look at another example, where we select only columns where the number of distinct values is less than 10:

In [38]:
# returns a list of booleans
columns_to_select = [frame.nunique()[0, 0] < 10 for frame in DT]
DT[:, columns_to_select].head(5)

<Frame#7fb7e0ff35a0 5x2>

In [39]:
matching_frames = [frame for frame in DT if frame.nunique()[0,0] < 10]
dt.cbind(matching_frames).head(5)

<Frame#7fb7e0d4ae40 5x2>

Or pass `matching_frames` to the `j` section in `DT`:

In [40]:
DT[:, matching_frames].head(5)

<Frame#7fb7e0ff3ab0 5x2>

## **Reordering Columns**

You can select columns in the order that you want:

In [41]:
columns_to_select = ['conservation', 'sleep_total', 'name']
DT[:, columns_to_select].head(5)

<Frame#7fb7e0d4a930 5x3>

To move some columns to the front, you could write a function to cover that:

In [42]:
def move_to_the_front(frame, front_columns):
    column_names = list(frame.names)
    for name in front_columns:
        column_names.remove(name)
    front_columns.extend(column_names)
    return front_columns

In [43]:
DT[:, move_to_the_front(DT, ['conservation', 'sleep_total'])].head(5)

<Frame#7fb7e102f210 5x11>

## **Column Names**

### Renaming Columns

Columns with new names can be created within the `j` section by passing a dictionary:

In [44]:
new_names = {"animal": f.name, "extinction_threat": f.conservation}
DT[:, f.sleep_total.extend(new_names)].head(5)

<Frame#7fb7e0ff3180 5x3>

You can also rename the columns via a dictionary that maps the old column name to the new column name, and assign it to ``DT.names``:

In [45]:
DT_copy = DT.copy()
DT_copy.names = {"name": "animal", "conservation": "extinction_threat"}
DT_copy[:, ['animal', 'sleep_total', 'extinction_threat']].head(5)


<Frame#7fb7e0ff37b0 5x3>

In [46]:
DT_copy.head(5)

<Frame#7fb7e0ff37e0 5x11>

### Reformatting all Column Names

You can use python's string functions to reformat column names.

Let's convert all column names to uppercase:

In [47]:
DT_copy.names = [name.upper() for name in DT.names] # or list(map(str.upper, DT.names))
DT_copy.head(5)

<Frame#7fb7e0d4af00 5x11>

Resources: 

- [datatable docs](https://datatable.readthedocs.io/en/latest/)

## Comments
<script src="https://utteranc.es/client.js"
        repo="samukweku/data-wrangling-blog"
        issue-term="title"
        theme="github-light"
        crossorigin="anonymous"
        async>
</script>